#### order brushing
- 先找出 deemed shop
- 再找出該 shop 下的 deemed buyers


In [1]:
import pandas as pd
from datetime import datetime
from tqdm import tqdm
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"


In [2]:
def gen_dayHrMin(user_clicks, time_col):
    # # 將 日-時-分 拆出來
#     user_clicks['year'] = user_clicks[time_col].apply(lambda x: int(x.split(' ')[0].split('-')[0]))
#     user_clicks['month'] = user_clicks[time_col].apply(lambda x: int(x.split(' ')[0].split('-')[1]))
    user_clicks['day'] = user_clicks[time_col].apply(lambda x: int(x.split(' ')[0].split('-')[2]))
    user_clicks['hour'] = user_clicks[time_col].apply(lambda x: int(x.split(' ')[1].split(':')[0]))
    user_clicks['minute'] = user_clicks[time_col].apply(lambda x: int(x.split(' ')[1].split(':')[1]))
    user_clicks['second'] = user_clicks[time_col].apply(lambda x: int(x.split(' ')[1].split(':')[2]))
#     user_clicks.drop(time_col, axis=1, inplace=True)
    return user_clicks

def gen_timeblock(df):
    df['timeblock'] = (df['day'] - 27) * 24 + df['hour']
    df['min_block'] = (df['day'] - 27) * 24 * 60 + df['hour'] * 60 + df['minute']
    df['sec_block'] = (df['day'] - 27) * 24 * 3600 + df['hour'] * 3600 + df['minute'] * 60 + df['second']
    df = df.sort_values('sec_block')
    return df


In [3]:
df = pd.read_csv('order_brush_order.csv')
df.isnull().sum()
len(df)
df['orderid'] = df['orderid'].astype(str)
df['shopid'] = df['shopid'].astype(str)
df['userid'] = df['userid'].astype(str)
df = gen_dayHrMin(df, 'event_time')
df = gen_timeblock(df)
df.head()


orderid       0
shopid        0
userid        0
event_time    0
dtype: int64

222750

orderid     shopid     userid           event_time  day  hour  \
150060  31075200506751    6042309   97707522  2019-12-27 00:00:00   27     0   
25985   31075200506752  104804492   97707522  2019-12-27 00:00:00   27     0   
81020   31075200506753    8715449   97707522  2019-12-27 00:00:00   27     0   
146598  31075201870570  190969466  170182475  2019-12-27 00:00:02   27     0   
80355   31075205798264    2859407   12532131  2019-12-27 00:00:05   27     0   

        minute  second  timeblock  min_block  sec_block  
150060       0       0          0          0          0  
25985        0       0          0          0          0  
81020        0       0          0          0          0  
146598       0       2          0          0          2  
80355        0       5          0          0          5

In [5]:
deemed_records_2 = list()
for shop in tqdm(df.shopid.unique()):
    tmp = df[df['shopid']==shop]
    for sec in tqdm(tmp.sec_block.unique()):
        tmp = tmp[(tmp['sec_block']>=sec)&(tmp['sec_block']<=sec+3600)].sort_values('sec_block')
        if len(tmp) > 0:
            concentrate_rate = len(tmp.orderid.values) / len(tmp.userid.unique())
            if concentrate_rate >= 3:
                print(shop, sec, sec+3600, concentrate_rate)
                protion_df = tmp.groupby(['userid'])['orderid'].count().reset_index()
                protion_df['portion'] = protion_df['orderid'] / protion_df['orderid'].sum()
                deemed_buyers = protion_df[protion_df['portion']==max(protion_df['portion'].values)].userid.unique()
                for deemed_buyer in deemed_buyers:
                    deemed_records_2.append([shop, deemed_buyer])




  0%|                                                                                        | 0/18770 [00:00<?, ?it/s]


  0%|                                                                                           | 0/26 [00:00<?, ?it/s]


100%|█████████████████████████████████████████████████████████████████████████████████| 26/26 [00:00<00:00, 960.40it/s]


  0%|                                                                                           | 0/36 [00:00<?, ?it/s]


100%|█████████████████████████████████████████████████████████████████████████████████| 36/36 [00:00<00:00, 789.10it/s]

  0%|                                                                                | 2/18770 [00:00<18:30, 16.90it/s]


  0%|                                                                                          | 0/171 [00:00<?, ?it/s]


 58%|██████████████████████████████████████████████▎                                 | 99/171 [00:00<00:00, 982.46it/s]


100%|██████████████████

 42%|███████████████████████████████▌                                            | 4727/11388 [00:04<00:06, 983.06it/s]


 42%|████████████████████████████████▏                                           | 4826/11388 [00:04<00:06, 968.35it/s]


 43%|████████████████████████████████▊                                           | 4925/11388 [00:05<00:06, 973.97it/s]


 44%|█████████████████████████████████▌                                          | 5024/11388 [00:05<00:06, 977.96it/s]


 45%|██████████████████████████████████▏                                         | 5123/11388 [00:05<00:06, 980.60it/s]


 46%|██████████████████████████████████▊                                         | 5222/11388 [00:05<00:06, 982.60it/s]


 47%|███████████████████████████████████▌                                        | 5321/11388 [00:05<00:06, 982.65it/s]


 48%|████████████████████████████████████▏                                       | 5420/11388 [00:05<00:06, 981.03it/s]


 48%|███████████████████

 98%|█████████████████████████████████████████████████████████████████████████▌ | 11163/11388 [00:11<00:00, 977.16it/s]


 99%|██████████████████████████████████████████████████████████████████████████▏| 11261/11388 [00:11<00:00, 974.31it/s]


100%|██████████████████████████████████████████████████████████████████████████▊| 11359/11388 [00:11<00:00, 975.14it/s]


100%|███████████████████████████████████████████████████████████████████████████| 11388/11388 [00:11<00:00, 980.20it/s]

  0%|                                                                             | 8/18770 [00:12<18:30:29,  3.55s/it]


  0%|                                                                                         | 0/2624 [00:00<?, ?it/s]


  4%|██▉                                                                            | 96/2624 [00:00<00:02, 957.23it/s]


  7%|█████▊                                                                        | 196/2624 [00:00<00:02, 967.51it/s]


 11%|████████▋           

 51%|████████████████████████████████████████                                       | 100/197 [00:00<00:00, 992.13it/s]


100%|███████████████████████████████████████████████████████████████████████████████| 197/197 [00:00<00:00, 979.74it/s]

  0%|                                                                             | 20/18770 [00:16<2:09:17,  2.42it/s]


  0%|                                                                                          | 0/102 [00:00<?, ?it/s]


 98%|█████████████████████████████████████████████████████████████████████████████▍ | 100/102 [00:00<00:00, 997.11it/s]


100%|███████████████████████████████████████████████████████████████████████████████| 102/102 [00:00<00:00, 978.16it/s]

  0%|                                                                             | 21/18770 [00:16<1:42:37,  3.05it/s]


  0%|                                                                                           | 0/96 [00:00<?, ?it/s]


100%|█████████████████████

100%|█████████████████████████████████████████████████████████████████████████████████| 13/13 [00:00<00:00, 894.12it/s]

  0%|▏                                                                              | 43/18770 [00:18<33:21,  9.36it/s]


  0%|                                                                                           | 0/69 [00:00<?, ?it/s]


100%|█████████████████████████████████████████████████████████████████████████████████| 69/69 [00:00<00:00, 982.70it/s]


  0%|                                                                                           | 0/42 [00:00<?, ?it/s]


100%|█████████████████████████████████████████████████████████████████████████████████| 42/42 [00:00<00:00, 984.96it/s]

  0%|▏                                                                              | 45/18770 [00:18<30:44, 10.15it/s]


  0%|                                                                                           | 0/76 [00:00<?, ?it/s]


100%|█████████████████████

...

100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 498.67it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 498.61it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 498.49it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 498.67it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████

  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 664.71it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 498.67it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 664.81it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 664.92it/s]

 99%|████████████████████

100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 665.45it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 664.92it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 398.96it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 498.67it/s]

100%|███████████████████████████████████████████████████████████████████████████▋| 18701/18770 [10:57<00:01, 41.60it/s]


  0%|                    

  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 664.71it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 665.02it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 665.55it/s]

100%|███████████████████████████████████████████████████████████████████████████▊| 18731/18770 [10:58<00:00, 41.72it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|████████████████████

100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 665.02it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 664.39it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 498.97it/s]

100%|███████████████████████████████████████████████████████████████████████████▉| 18761/18770 [10:59<00:00, 41.60it/s]


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 664.81it/s]


  0%|                    

In [6]:
df_result_2 = pd.DataFrame(deemed_records_2)
df_result_2.columns = ['shopid','userid']
df_result_2['shopid'] = df_result_2['shopid'].astype(str)
df_result_2['userid'] = df_result_2['userid'].astype(str)
df_result_2.drop_duplicates(inplace=True)
df_result_2 = df_result_2.groupby('shopid').agg({'userid': '&'.join}).reset_index()
df_result_2


shopid               userid
0   100446829              2434757
1       10536               672345
2   106051591              1276208
3   119595148             17722130
4   123401085             12869645
5   129113839            215408773
6   130098983            179997347
7   132583615            152710183
8   134418456            214778616
9   141025402               613919
10  144365607            214411855
11  153444897            169948888
12  153672697            214778616
13  155016230            188431260
14  155143347  156202149&214265994
15  157939195             69563623
16   15920950            211907762
17  161196859            180862522
18  162292584            119654795
19   16246487            214300427
20  163351089            214778616
21  163968828             78903959
22  173454640             12597591
23  181009364            214208720
24  182630287            158048102
25  191285578            214925963
26  201428849             89254393
27  203070501            189834273
28  203440274             73308605
29  210197928             52867898
30  213141071            213646699
31    3124091            214568881
32   35590237              2097773
33   50682734            214365114
34   63001745            101866283
35   64369518            172591713
36   71168001             11053808
37     731606             75558350
38   78837196             78903959
39   80049863            123158564

In [94]:
# output deemed_records
deemed_records = list()
for shop in tqdm(df.shopid.unique()):
    tmp = df[df['shopid']==shop].sort_values('event_time')
    for block in tmp.timeblock.unique():
        concentrate_rate = len(tmp[tmp['timeblock']==block].orderid.values) / len(tmp[tmp['timeblock']==block].userid.unique())
        if concentrate_rate >= 3:
            print(shop, block, concentrate_rate)
            protion_df = tmp[(tmp['timeblock']==block)|(tmp['timeblock']==block+1)].groupby(['userid'])['orderid'].count().reset_index()
            protion_df['portion'] = protion_df['orderid'] / protion_df['orderid'].sum()
            deemed_buyers = protion_df[protion_df['portion']==max(protion_df['portion'].values)].userid.unique()
            for deemed_buyer in deemed_buyers:
                deemed_records.append([shop, deemed_buyer])
                 
        if concentrate_rate >= 3:
            print(shop, block, block+1, concentrate_rate)
            protion_df = tmp[(tmp['timeblock']==block)|(tmp['timeblock']==block+1)].groupby(['userid'])['orderid'].count().reset_index()
            protion_df['portion'] = protion_df['orderid'] / protion_df['orderid'].sum()
            deemed_buyers = protion_df[protion_df['portion']==max(protion_df['portion'].values)].userid.unique()
            for deemed_buyer in deemed_buyers:
                deemed_records.append([shop, deemed_buyer])




  0%|                                                                                        | 0/18770 [00:00<?, ?it/s]

  0%|                                                                                | 1/18770 [00:00<50:20,  6.21it/s]

  0%|                                                                              | 2/18770 [00:00<1:04:16,  4.87it/s]

  0%|                                                                                | 6/18770 [00:00<47:26,  6.59it/s]

  0%|                                                                                | 8/18770 [00:00<37:59,  8.23it/s]

  0%|                                                                               | 10/18770 [00:00<31:55,  9.79it/s]

  0%|                                                                               | 12/18770 [00:00<27:39, 11.30it/s]

  0%|                                                                               | 14/18770 [00:01<30:30, 10.25it/s]

  0%|                         

18190345 52 3.0
18190345 52 3.0




  0%|                                                                               | 25/18770 [00:02<39:51,  7.84it/s]

  0%|                                                                               | 27/18770 [00:02<42:13,  7.40it/s]

  0%|                                                                               | 29/18770 [00:02<40:02,  7.80it/s]

  0%|▏                                                                              | 30/18770 [00:03<43:54,  7.11it/s]

  0%|▏                                                                              | 32/18770 [00:03<37:47,  8.26it/s]

  0%|▏                                                                              | 33/18770 [00:03<48:51,  6.39it/s]

  0%|▏                                                                              | 35/18770 [00:03<42:53,  7.28it/s]

  0%|▏                                                                              | 36/18770 [00:03<45:08,  6.92it/s]

  0%|▏                        

27476241 9 5.0
27476241 10 4.0




  0%|▏                                                                              | 46/18770 [00:04<32:35,  9.58it/s]

  0%|▏                                                                              | 48/18770 [00:04<31:16,  9.98it/s]

  0%|▏                                                                              | 51/18770 [00:05<28:06, 11.10it/s]

  0%|▏                                                                              | 53/18770 [00:05<31:04, 10.04it/s]

  0%|▏                                                                              | 56/18770 [00:05<28:19, 11.01it/s]

  0%|▏                                                                              | 58/18770 [00:05<27:11, 11.47it/s]

  0%|▎                                                                              | 60/18770 [00:05<25:04, 12.43it/s]

  0%|▎                                                                              | 62/18770 [00:06<24:52, 12.54it/s]

  0%|▎                        

...



 96%|████████████████████████████████████████████████████████████████████████▋   | 17963/18770 [11:36<00:18, 42.54it/s]

 96%|████████████████████████████████████████████████████████████████████████▊   | 17968/18770 [11:36<00:18, 43.51it/s]

 96%|████████████████████████████████████████████████████████████████████████▊   | 17973/18770 [11:36<00:18, 43.56it/s]

 96%|████████████████████████████████████████████████████████████████████████▊   | 17978/18770 [11:36<00:18, 43.85it/s]

 96%|████████████████████████████████████████████████████████████████████████▊   | 17983/18770 [11:36<00:17, 44.28it/s]

 96%|████████████████████████████████████████████████████████████████████████▊   | 17988/18770 [11:36<00:17, 44.77it/s]

 96%|████████████████████████████████████████████████████████████████████████▊   | 17993/18770 [11:36<00:17, 44.81it/s]

 96%|████████████████████████████████████████████████████████████████████████▊   | 17998/18770 [11:37<00:17, 44.54it/s]

 96%|█████████████████████████

123401085 115 4.0
123401085 115 4.0




 98%|██████████████████████████████████████████████████████████████████████████▍ | 18393/18770 [11:46<00:08, 43.87it/s]

 98%|██████████████████████████████████████████████████████████████████████████▍ | 18398/18770 [11:46<00:08, 44.17it/s]

 98%|██████████████████████████████████████████████████████████████████████████▌ | 18403/18770 [11:46<00:08, 41.66it/s]

 98%|██████████████████████████████████████████████████████████████████████████▌ | 18408/18770 [11:46<00:08, 40.91it/s]

 98%|██████████████████████████████████████████████████████████████████████████▌ | 18413/18770 [11:46<00:08, 41.62it/s]

 98%|██████████████████████████████████████████████████████████████████████████▌ | 18418/18770 [11:46<00:08, 41.86it/s]

 98%|██████████████████████████████████████████████████████████████████████████▌ | 18423/18770 [11:46<00:08, 41.96it/s]

 98%|██████████████████████████████████████████████████████████████████████████▌ | 18428/18770 [11:46<00:08, 42.15it/s]

 98%|█████████████████████████

155016230 117 3.0
155016230 117 3.0




 99%|███████████████████████████████████████████████████████████████████████████ | 18553/18770 [11:49<00:05, 42.93it/s]

 99%|███████████████████████████████████████████████████████████████████████████▏| 18558/18770 [11:49<00:04, 43.45it/s]

 99%|███████████████████████████████████████████████████████████████████████████▏| 18563/18770 [11:50<00:04, 44.17it/s]

 99%|███████████████████████████████████████████████████████████████████████████▏| 18568/18770 [11:50<00:04, 44.28it/s]

 99%|███████████████████████████████████████████████████████████████████████████▏| 18573/18770 [11:50<00:04, 44.11it/s]

 99%|███████████████████████████████████████████████████████████████████████████▏| 18578/18770 [11:50<00:04, 43.94it/s]

 99%|███████████████████████████████████████████████████████████████████████████▏| 18583/18770 [11:50<00:04, 44.23it/s]

 99%|███████████████████████████████████████████████████████████████████████████▎| 18588/18770 [11:50<00:04, 44.85it/s]

 99%|█████████████████████████

In [95]:
df_result = pd.DataFrame(deemed_records)
df_result.columns = ['shopid','userid']
df_result['shopid'] = df_result['shopid'].astype(str)
df_result['userid'] = df_result['userid'].astype(str)
df_result.drop_duplicates(inplace=True)
df_result = df_result.groupby('shopid').agg({'userid': '&'.join}).reset_index()
df_result


shopid     userid
0    100446829    2434757
1     10199219    8405753
2     10206302   95058664
3    103715156  214226569
4        10402      77819
..         ...        ...
252   97167904  214778616
253   98481320  124597967
254   98793086  142710562
255   99067259  108402614
256   99836251  197470611

[257 rows x 2 columns]

In [8]:
test = df_result_2.copy()
for s in tqdm(df.shopid.unique()):
    if s not in df_result_2.shopid.unique():
        test = test.append(pd.DataFrame([[s,0]],columns=['shopid','userid']), ignore_index=True)
        
test



  0%|                                                                                        | 0/18770 [00:00<?, ?it/s]

  0%|▍                                                                             | 92/18770 [00:00<00:20, 912.78it/s]

  1%|▋                                                                            | 180/18770 [00:00<00:20, 901.95it/s]

  1%|█                                                                            | 267/18770 [00:00<00:20, 890.02it/s]

  2%|█▍                                                                           | 354/18770 [00:00<00:20, 881.85it/s]

  2%|█▊                                                                           | 440/18770 [00:00<00:20, 873.20it/s]

  3%|██▏                                                                          | 525/18770 [00:00<00:21, 865.34it/s]

  3%|██▍                                                                          | 609/18770 [00:00<00:21, 855.56it/s]

  4%|██▊                      

 28%|█████████████████████▎                                                      | 5257/18770 [00:06<00:18, 726.03it/s]

 28%|█████████████████████▌                                                      | 5331/18770 [00:06<00:18, 729.54it/s]

 29%|█████████████████████▉                                                      | 5405/18770 [00:06<00:18, 729.90it/s]

 29%|██████████████████████▏                                                     | 5479/18770 [00:07<00:18, 732.32it/s]

 30%|██████████████████████▍                                                     | 5554/18770 [00:07<00:17, 735.87it/s]

 30%|██████████████████████▊                                                     | 5628/18770 [00:07<00:17, 732.13it/s]

 30%|███████████████████████                                                     | 5702/18770 [00:07<00:17, 731.71it/s]

 31%|███████████████████████▍                                                    | 5776/18770 [00:07<00:17, 732.50it/s]

 31%|███████████████████████▋   

 53%|████████████████████████████████████████                                   | 10037/18770 [00:13<00:12, 673.97it/s]

 54%|████████████████████████████████████████▍                                  | 10106/18770 [00:13<00:12, 677.18it/s]

 54%|████████████████████████████████████████▋                                  | 10174/18770 [00:13<00:12, 675.46it/s]

 55%|████████████████████████████████████████▉                                  | 10242/18770 [00:13<00:12, 673.25it/s]

 55%|█████████████████████████████████████████▏                                 | 10310/18770 [00:13<00:12, 668.73it/s]

 55%|█████████████████████████████████████████▍                                 | 10377/18770 [00:14<00:12, 667.58it/s]

 56%|█████████████████████████████████████████▋                                 | 10444/18770 [00:14<00:12, 667.82it/s]

 56%|█████████████████████████████████████████▉                                 | 10511/18770 [00:14<00:12, 666.89it/s]

 56%|███████████████████████████

 77%|█████████████████████████████████████████████████████████▌                 | 14405/18770 [00:20<00:07, 618.30it/s]

 77%|█████████████████████████████████████████████████████████▊                 | 14467/18770 [00:20<00:06, 618.27it/s]

 77%|██████████████████████████████████████████████████████████                 | 14529/18770 [00:20<00:06, 618.34it/s]

 78%|██████████████████████████████████████████████████████████▎                | 14592/18770 [00:20<00:06, 619.42it/s]

 78%|██████████████████████████████████████████████████████████▌                | 14654/18770 [00:20<00:06, 619.14it/s]

 78%|██████████████████████████████████████████████████████████▊                | 14716/18770 [00:20<00:06, 618.86it/s]

 79%|███████████████████████████████████████████████████████████                | 14778/18770 [00:20<00:06, 616.90it/s]

 79%|███████████████████████████████████████████████████████████▎               | 14840/18770 [00:21<00:06, 617.29it/s]

 79%|███████████████████████████

 98%|█████████████████████████████████████████████████████████████████████████▋ | 18437/18770 [00:27<00:00, 552.80it/s]

 99%|█████████████████████████████████████████████████████████████████████████▉ | 18495/18770 [00:27<00:00, 560.30it/s]

 99%|██████████████████████████████████████████████████████████████████████████▏| 18554/18770 [00:27<00:00, 567.58it/s]

 99%|██████████████████████████████████████████████████████████████████████████▎| 18611/18770 [00:27<00:00, 567.05it/s]

 99%|██████████████████████████████████████████████████████████████████████████▌| 18669/18770 [00:27<00:00, 568.70it/s]

100%|██████████████████████████████████████████████████████████████████████████▊| 18727/18770 [00:27<00:00, 569.11it/s]

100%|███████████████████████████████████████████████████████████████████████████| 18770/18770 [00:27<00:00, 675.69it/s]

shopid    userid
0      100446829   2434757
1          10536    672345
2      106051591   1276208
3      119595148  17722130
4      123401085  12869645
...          ...       ...
18765  173249173         0
18766  212058195         0
18767     577768         0
18768  162561288         0
18769  203090989         0

[18770 rows x 2 columns]

In [52]:
df_result.to_csv('partial_result.csv')

In [9]:
test.to_csv('200613_4th_submission.csv', index=0)

In [10]:
test['userid'] = test['userid'].astype(str)
test[test['userid'].str.contains('&')]

shopid               userid
14  155143347  156202149&214265994

In [17]:
for sh in df_result_2.shopid.unique():
    df[df['shopid']==sh]

orderid     shopid   userid           event_time  day  hour  \
184386  31198240318279  100446829  2434757  2019-12-28 10:10:41   28    10   
78035   31198725408292  100446829  2434757  2019-12-28 10:18:46   28    10   
32853   31198845226458  100446829  2434757  2019-12-28 10:20:45   28    10   
100825  31198992917834  100446829  2434757  2019-12-28 10:23:12   28    10   

        minute  second  timeblock  min_block  sec_block  
184386      10      41         34       2050     123041  
78035       18      46         34       2058     123526  
32853       20      45         34       2060     123645  
100825      23      12         34       2063     123792

orderid shopid     userid           event_time  day  hour  \
30685   31115953007150  10536     672345  2019-12-27 11:19:13   27    11   
76124   31116816860970  10536     672345  2019-12-27 11:33:37   27    11   
117649  31117448503731  10536     672345  2019-12-27 11:44:08   27    11   
195783  31138151853986  10536     672345  2019-12-27 17:29:12   27    17   
39004   31139160444394  10536     672345  2019-12-27 17:46:00   27    17   
59058   31139726362042  10536     672345  2019-12-27 17:55:26   27    17   
13614   31193005938624  10536  153387696  2019-12-28 08:43:25   28     8   
133517  31210467189739  10536  106083615  2019-12-28 13:34:27   28    13   
222612  31216027417499  10536     672345  2019-12-28 15:07:07   28    15   
94285   31216637148289  10536     672345  2019-12-28 15:17:17   28    15   
103427  31281842070668  10536  214403263  2019-12-29 09:24:02   29     9   
135484  31333417208231  10536  214403263  2019-12-29 23:43:37   29    23   
134777  31354950199856  10536   70540468  2019-12-30 05:42:30   30     5   

        minute  second  timeblock  min_block  sec_block  
30685       19      13         11        679      40753  
76124       33      37         11        693      41617  
117649      44       8         11        704      42248  
195783      29      12         17       1049      62952  
39004       46       0         17       1066      63960  
59058       55      26         17       1075      64526  
13614       43      25         32       1963     117805  
133517      34      27         37       2254     135267  
222612       7       7         39       2347     140827  
94285       17      17         39       2357     141437  
103427      24       2         57       3444     206642  
135484      43      37         71       4303     258217  
134777      42      30         77       4662     279750

orderid     shopid    userid           event_time  day  hour  \
143219  31159909728471  106051591   1276208  2019-12-27 23:31:49   27    23   
146484  31160592713651  106051591   1276208  2019-12-27 23:43:12   27    23   
152531  31161132708454  106051591   1276208  2019-12-27 23:52:12   27    23   
159975  31161653013153  106051591   1276208  2019-12-28 00:00:53   28     0   
26226   31481701954535  106051591  89786967  2019-12-31 16:55:01   31    16   

        minute  second  timeblock  min_block  sec_block  
143219      31      49         23       1411      84709  
146484      43      12         23       1423      85392  
152531      52      12         23       1432      85932  
159975       0      53         24       1440      86453  
26226       55       1        112       6775     406501

orderid     shopid     userid           event_time  day  hour  \
75402   31136381835376  119595148   17722130  2019-12-27 16:59:42   27    16   
41363   31136954724328  119595148   17722130  2019-12-27 17:09:14   27    17   
132126  31137152187853  119595148   17722130  2019-12-27 17:12:32   27    17   
193861  31256625256580  119595148   30924507  2019-12-29 02:23:46   29     2   
217148  31289686241851  119595148  214856186  2019-12-29 11:34:47   29    11   
164200  31306416397973  119595148   58509644  2019-12-29 16:13:36   29    16   
80642   31307161236125  119595148   96907036  2019-12-29 16:26:02   29    16   
29923   31312796258858  119595148   14328285  2019-12-29 17:59:56   29    17   
61350   31314782587925  119595148   59569769  2019-12-29 18:33:03   29    18   
70415   31322632213049  119595148   49740620  2019-12-29 20:43:53   29    20   
63935   31331767757565  119595148   87291506  2019-12-29 23:16:07   29    23   
138675  31374202641739  119595148   14302332  2019-12-30 11:03:22   30    11   
93533   31403488434740  119595148  172487817  2019-12-30 19:11:28   30    19   
222349  31448051139403  119595148   23027288  2019-12-31 07:34:12   31     7   
185969  31474598884669  119595148  119200034  2019-12-31 14:56:39   31    14   

        minute  second  timeblock  min_block  sec_block  
75402       59      42         16       1019      61182  
41363        9      14         17       1029      61754  
132126      12      32         17       1032      61952  
193861      23      46         50       3023     181426  
217148      34      47         59       3574     214487  
164200      13      36         64       3853     231216  
80642       26       2         64       3866     231962  
29923       59      56         65       3959     237596  
61350       33       3         66       3993     239583  
70415       43      53         68       4123     247433  
63935       16       7         71       4276     256567  
138675       3      22         83       4983     299002  
93533       11      28         91       5471     328288  
222349      34      12        103       6214     372852  
185969      56      39        110       6656     399399

orderid     shopid    userid           event_time  day  hour  \
210715  31491062994911  123401085  12869645  2019-12-31 19:31:02   31    19   
99926   31491263671065  123401085  12869645  2019-12-31 19:34:23   31    19   
81253   31491370985048  123401085  12869645  2019-12-31 19:36:10   31    19   
88572   31491537156944  123401085  12869645  2019-12-31 19:38:57   31    19   

        minute  second  timeblock  min_block  sec_block  
210715      31       2        115       6931     415862  
99926       34      23        115       6934     416063  
81253       36      10        115       6936     416170  
88572       38      57        115       6938     416337

...

orderid    shopid     userid           event_time  day  hour  \
200997  31285680235596  64369518  172591713  2019-12-29 10:28:00   29    10   
197066  31285805869936  64369518  172591713  2019-12-29 10:30:06   29    10   
210425  31286301342631  64369518  172591713  2019-12-29 10:38:21   29    10   
188832  31301323324424  64369518  205743345  2019-12-29 14:48:43   29    14   
204509  31328345241648  64369518  170087781  2019-12-29 22:19:06   29    22   
105486  31385178049788  64369518     136893  2019-12-30 14:06:18   30    14   

        minute  second  timeblock  min_block  sec_block  
200997      28       0         58       3508     210480  
197066      30       6         58       3510     210606  
210425      38      21         58       3518     211101  
188832      48      43         62       3768     226123  
204509      19       6         70       4219     253146  
105486       6      18         86       5166     309978

orderid    shopid     userid           event_time  day  hour  \
92869   31224977465703  71168001   11053808  2019-12-28 17:36:17   28    17   
174678  31225265216251  71168001   11053808  2019-12-28 17:41:05   28    17   
26515   31225367971794  71168001   11053808  2019-12-28 17:42:47   28    17   
137660  31242389162972  71168001   52529046  2019-12-28 22:26:29   28    22   
125473  31242809999182  71168001   41279588  2019-12-28 22:33:29   28    22   
122503  31247108633980  71168001  198538254  2019-12-28 23:45:09   28    23   
58889   31251519997234  71168001    9062509  2019-12-29 00:58:39   29     0   
142032  31279586844198  71168001  112171733  2019-12-29 08:46:27   29     8   
205785  31316530279279  71168001   78343281  2019-12-29 19:02:10   29    19   
137210  31330961873807  71168001   88698332  2019-12-29 23:02:42   29    23   
20226   31370364352569  71168001   40939151  2019-12-30 09:59:24   30     9   
174827  31383286346687  71168001   11926671  2019-12-30 13:34:46   30    13   
167156  31468456766399  71168001   89078736  2019-12-31 13:14:16   31    13   
144121  31475840483732  71168001   45410917  2019-12-31 15:17:20   31    15   
169358  31477738399502  71168001  102178983  2019-12-31 15:48:58   31    15   
130604  31482848789482  71168001   17453486  2019-12-31 17:14:08   31    17   
135053  31493142382665  71168001    7074016  2019-12-31 20:05:42   31    20   
140627  31498659278436  71168001   15459880  2019-12-31 21:37:39   31    21   
139699  31500999196420  71168001   55298413  2019-12-31 22:16:40   31    22   
10165   31504383754563  71168001  197878522  2019-12-31 23:13:04   31    23   

        minute  second  timeblock  min_block  sec_block  
92869       36      17         41       2496     149777  
174678      41       5         41       2501     150065  
26515       42      47         41       2502     150167  
137660      26      29         46       2786     167189  
125473      33      29         46       2793     167609  
122503      45       9         47       2865     171909  
58889       58      39         48       2938     176319  
142032      46      27         56       3406     204387  
205785       2      10         67       4022     241330  
137210       2      42         71       4262     255762  
20226       59      24         81       4919     295164  
174827      34      46         85       5134     308086  
167156      14      16        109       6554     393256  
144121      17      20        111       6677     400640  
169358      48      58        111       6708     402538  
130604      14       8        113       6794     407648  
135053       5      42        116       6965     417942  
140627      37      39        117       7057     423459  
139699      16      40        118       7096     425800  
10165       13       4        119       7153     429184

orderid  shopid    userid           event_time  day  hour  \
132905  31122566048448  731606  75558350  2019-12-27 13:09:26   27    13   
60765   31123831111474  731606  75558350  2019-12-27 13:30:31   27    13   
21994   31123890480597  731606  75558350  2019-12-27 13:31:30   27    13   
92335   31211332143641  731606  75558350  2019-12-28 13:48:53   28    13   
198583  31211397728926  731606  75558350  2019-12-28 13:49:57   28    13   
133961  31211458933074  731606  75558350  2019-12-28 13:50:58   28    13   

        minute  second  timeblock  min_block  sec_block  
132905       9      26         13        789      47366  
60765       30      31         13        810      48631  
21994       31      30         13        811      48690  
92335       48      53         37       2268     136133  
198583      49      57         37       2269     136197  
133961      50      58         37       2270     136258

orderid    shopid    userid           event_time  day  hour  \
178891  31127546872349  78837196  78903959  2019-12-27 14:32:27   27    14   
171915  31127582299599  78837196  78903959  2019-12-27 14:33:03   27    14   
168692  31127616862243  78837196  78903959  2019-12-27 14:33:37   27    14   
84554   31127731820569  78837196  78903959  2019-12-27 14:35:32   27    14   
149619  31206225666528  78837196  64372009  2019-12-28 12:23:45   28    12   

        minute  second  timeblock  min_block  sec_block  
178891      32      27         14        872      52347  
171915      33       3         14        873      52383  
168692      33      37         14        873      52417  
84554       35      32         14        875      52532  
149619      23      45         36       2183     131025

orderid    shopid     userid           event_time  day  hour  \
35589   31129111942938  80049863  123158564  2019-12-27 14:58:31   27    14   
194     31129438449839  80049863  123158564  2019-12-27 15:03:58   27    15   
111284  31129542451076  80049863  123158564  2019-12-27 15:05:42   27    15   
68473   31130475478979  80049863  123158564  2019-12-27 15:21:15   27    15   
4712    31210356462413  80049863  184977884  2019-12-28 13:32:36   28    13   
169646  31213474750984  80049863  123158564  2019-12-28 14:24:34   28    14   
204611  31289294382989  80049863   33331805  2019-12-29 11:28:14   29    11   
179352  31330618744083  80049863   40548079  2019-12-29 22:56:58   29    22   
202129  31334811602278  80049863  126228294  2019-12-30 00:06:52   30     0   
200279  31336374130519  80049863  126228294  2019-12-30 00:32:55   30     0   
9689    31380272353370  80049863   64484236  2019-12-30 12:44:32   30    12   

        minute  second  timeblock  min_block  sec_block  
35589       58      31         14        898      53911  
194          3      58         15        903      54238  
111284       5      42         15        905      54342  
68473       21      15         15        921      55275  
4712        32      36         37       2252     135156  
169646      24      34         38       2304     138274  
204611      28      14         59       3568     214094  
179352      56      58         70       4256     255418  
202129       6      52         72       4326     259612  
200279      32      55         72       4352     261175  
9689        44      32         84       5084     305072